# Design Patterns for ML Applications



*(a.k.a. Turning Data Science Experiments into Real Software)*

Machine Learning projects start like college dorm experiments — chaotic, unstructured, and full of unexplained results.

But when you’re building **production-grade ML systems**, you can’t have 17 versions of `model_final_v2_latest_real_final.pkl` lying around.
You need **design patterns** — reusable templates for structuring logic, managing models, and keeping your sanity.

---

### ☕ Why Design Patterns Matter

Design patterns aren’t just fancy names for things you already do — they’re **battle-tested blueprints** that prevent your codebase from turning into a Frankenstein’s notebook.

> “Patterns are how senior engineers look calm while solving the same problem for the 47th time.”

For ML systems, these patterns make the difference between:

* a messy prototype that dies after one Kaggle win,
* and a robust ML service that survives Black Friday traffic.

---

## 🎯 1. The Strategy Pattern

*(aka “Choose Your Model Like You Choose Your Coffee Blend”)*

You have multiple models — linear regression, random forest, XGBoost, neural nets — each suited for different data moods.

Instead of using `if model == "xgboost": ...` everywhere, use the **Strategy Pattern** to switch models dynamically.

---

#### 💻 Example:

```python
class ModelStrategy:
    def train(self, data):
        raise NotImplementedError

class LinearRegressionStrategy(ModelStrategy):
    def train(self, data):
        print("Training Linear Regression Model")

class XGBoostStrategy(ModelStrategy):
    def train(self, data):
        print("Training XGBoost Model")

class ModelTrainer:
    def __init__(self, strategy: ModelStrategy):
        self.strategy = strategy

    def execute(self, data):
        self.strategy.train(data)
```

```python
# Switch model strategies easily
trainer = ModelTrainer(XGBoostStrategy())
trainer.execute(data="sales_data")
```

Now your business app can swap models faster than marketing changes priorities. 📈➡️📉➡️📈

---

### 🧱 2. The Factory Pattern

*(aka “Stop Manually Building Models Like It’s 2015”)*

When your system needs to create different types of objects (e.g., models, preprocessors, or data sources) at runtime — use the **Factory Pattern**.

Think of it as a **model factory** — it builds the right thing, so you don’t have to remember every parameter.

---

#### 💻 Example:

```python
class ModelFactory:
    @staticmethod
    def create_model(model_type):
        if model_type == "linear":
            return LinearRegression()
        elif model_type == "xgboost":
            return XGBRegressor()
        elif model_type == "lstm":
            return LSTMModel()
        else:
            raise ValueError("Unknown model type")

model = ModelFactory.create_model("xgboost")
```

Now when your boss says, “Can we test a neural net?” you say, “Sure — 3 lines of code,” instead of, “Give me 3 weeks.”

---

### 🧠 3. The Pipeline Pattern

*(a.k.a. The Assembly Line of ML)*

This one’s an ML classic.
The **Pipeline Pattern** structures your workflow into clear, modular steps — from raw data to predictions.

Each step is independent, testable, and replaceable.

---

#### 💻 Example:

```python
class Pipeline:
    def __init__(self, steps):
        self.steps = steps

    def run(self, data):
        for step in self.steps:
            data = step(data)
        return data

def load_data(_):
    print("Loading data")
    return [1, 2, 3]

def scale_data(data):
    print("Scaling data")
    return [x / 10 for x in data]

def predict(data):
    print("Predicting")
    return [x * 2 for x in data]

pipeline = Pipeline([load_data, scale_data, predict])
print(pipeline.run(None))
```

Output:

```
Loading data
Scaling data
Predicting
[0.2, 0.4, 0.6]
```

Boom — you’ve got a reusable ML pipeline.
Change one step, and the rest keeps flowing like a well-oiled factory belt. 🏭

---

### 💾 4. The Singleton Pattern

*(a.k.a. “Only One Model to Rule Them All”)*

You don’t want multiple versions of the same model floating around in memory — especially if it’s 500MB of neural net goodness.

The **Singleton Pattern** ensures that only one instance of an object (like your trained model or logger) exists across the entire app.

---

#### 💻 Example:

```python
class ModelSingleton:
    _instance = None

    def __new__(cls, model_path):
        if cls._instance is None:
            print("Loading model once...")
            cls._instance = super().__new__(cls)
            cls._instance.model = cls.load_model(model_path)
        return cls._instance

    @staticmethod
    def load_model(path):
        return f"Model loaded from {path}"

# Both refer to the same instance
m1 = ModelSingleton("model.pkl")
m2 = ModelSingleton("model.pkl")

print(m1 is m2)  # True
```

This prevents “model reloading madness” — that moment when your API takes 10 seconds for every call because it keeps reloading weights. 🧠💀

---

### 🕸️ 5. The Observer Pattern

*(a.k.a. “Let Everyone Know When the Model Breaks”)

In business ML systems, when something important happens — model retrained, data drift detected, new price strategy deployed — you often need to **notify multiple services**.

The **Observer Pattern** is perfect for this.

---

#### 💻 Example:

```python
class Observer:
    def update(self, message):
        pass

class SlackNotifier(Observer):
    def update(self, message):
        print(f"Slack: {message}")

class LogService(Observer):
    def update(self, message):
        print(f"Log: {message}")

class ModelMonitor:
    def __init__(self):
        self.subscribers = []

    def attach(self, observer):
        self.subscribers.append(observer)

    def notify(self, message):
        for sub in self.subscribers:
            sub.update(message)
```

```python
monitor = ModelMonitor()
monitor.attach(SlackNotifier())
monitor.attach(LogService())

monitor.notify("Model accuracy dropped below 80% 🚨")
```

Result:

```
Slack: Model accuracy dropped below 80% 🚨
Log: Model accuracy dropped below 80% 🚨
```

Now everyone gets the bad news at the same time. Efficient suffering.

---

### ⚙️ 6. The Repository Pattern

*(a.k.a. “Data Access with a Brain”)*

You don’t want every part of your system directly poking your database like an overenthusiastic intern.
The **Repository Pattern** creates a clean layer between business logic and data access.

---

#### 💻 Example:

```python
class SalesRepository:
    def __init__(self, db):
        self.db = db

    def get_sales(self, date):
        return self.db.query(f"SELECT * FROM sales WHERE date = '{date}'")

class SalesService:
    def __init__(self, repo):
        self.repo = repo

    def calculate_revenue(self, date):
        sales = self.repo.get_sales(date)
        return sum(s['price'] for s in sales)
```

Now, when you switch databases, you just replace the repository — not your entire logic.

> Database changes shouldn’t trigger existential crises.

---

### 🤖 7. The Command Pattern

*(a.k.a. “Schedule That Retrain Like a Pro”)*

Want to trigger retraining, evaluation, or deployments from a queue or scheduler?
Wrap those tasks as **commands** — reusable, pluggable operations.

---

#### 💻 Example:

```python
class Command:
    def execute(self):
        pass

class RetrainModelCommand(Command):
    def execute(self):
        print("Retraining model...")

class UpdateDashboardCommand(Command):
    def execute(self):
        print("Updating dashboard...")

class Scheduler:
    def run(self, commands):
        for command in commands:
            command.execute()
```

```python
scheduler = Scheduler()
scheduler.run([RetrainModelCommand(), UpdateDashboardCommand()])
```

Now you have a system where cron jobs or message queues can trigger ML tasks like a boss. 🕹️

---

### 🧩 Bonus: Combining Patterns Like a Pro

Real ML systems are **pattern cocktails**:

* Factory + Strategy → Dynamic model selection
* Pipeline + Observer → Real-time monitoring
* Singleton + Repository → Shared model & data access

Together, they form scalable, reusable, production-grade ML infrastructure.

---

### 💬 Final Thoughts

Design patterns don’t make you “corporate” — they make your code **survive success**.
Because once your model actually works, everyone will want to use it — and you’ll need a system that doesn’t collapse under popularity.

> “Write ML code like your future company depends on it — because it might.” 🚀

---

In [ ]:
# Your code here